In [1]:
print("GJ")

GJ


In [2]:
from qiskit_aer import AerSimulator
from math import pi
import matplotlib.pyplot as plt

from HQGA import problems_m as p
from HQGA import hqga_algorithm
from HQGA import hqga_utils
from HQGA import utils
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder, StandardScaler
from qiskit_ibm_runtime import QiskitRuntimeService


# other libraries
from sklearn.datasets import load_iris
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import  accuracy_score
import os

In [4]:
f_path = "dim_under_15/balanced/processed_Dishonest Internet users.csv"

csv = pd.read_csv(f_path)

print(csv)

     CT_range_4  CU_range_1  LT_range_4  sport  untrustworthy
0             3           0           3      3              1
1             0           2           3      3              0
2             1           0           3      3              0
3             2           0           3      3              0
4             3           0           3      3              1
..          ...         ...         ...    ...            ...
316           1           0           1      2              1
317           0           0           0      2              0
318           0           0           0      2              0
319           0           0           0      2              0
320           1           0           1      2              1

[321 rows x 5 columns]


In [4]:
target = csv.columns[-1]
X = csv.drop([target], axis=1)
y = csv[target]

print(X)
print(y)


# Split data into train and test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
train_df = pd.concat([X_train, y_train], axis=1)
test_df = pd.concat([X_test, y_test], axis=1)

scaler = StandardScaler()
train_x_sc = scaler.fit_transform(X_train)
test_x_sc = scaler.transform(X_test)

model = RandomForestClassifier(n_estimators=100, random_state=42)

model.fit(train_x_sc, y_train)

model

     CT_range_4  CU_range_1  LT_range_4  sport
0             3           0           3      3
1             0           2           3      3
2             1           0           3      3
3             2           0           3      3
4             3           0           3      3
..          ...         ...         ...    ...
316           1           0           1      2
317           0           0           0      2
318           0           0           0      2
319           0           0           0      2
320           1           0           1      2

[321 rows x 4 columns]
0      1
1      0
2      0
3      0
4      1
      ..
316    1
317    0
318    0
319    0
320    1
Name: untrustworthy, Length: 321, dtype: int64


RandomForestClassifier(random_state=42)

In [5]:
y_pred = model.predict(test_x_sc)
score = accuracy_score(y_test, y_pred)
print("accuracy_score: ", score)

accuracy_score:  1.0


In [11]:
def runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware = False):

    num_feat = train_x_sc.shape[1]

    global device_features, problem, params, circuit, gBest, chromosome_evolution, bests
    problem = p.FeatureSelection(num_feat, train_x_sc, y_train, test_x_sc, y_test)    
    if real_quantum_hardware:
        service = QiskitRuntimeService(channel="ibm_quantum", token="c1c57019a5ee715b66178367feda161fa8d15bc0b0a8e490516ca1fb4abc251ef94eb9822e6e7bae111a7ed6c591b80c3ea8cbcdbac26d4f431288f7e4cec930")
        backend = service.least_busy(simulator=False, operational=True)
        print("backend: ",backend)
        device_features=hqga_utils.device(backend, isReal = True)
    else:
        backend = AerSimulator()
        device_features=hqga_utils.device(backend, isReal = False)

    k = 30 // num_feat
    print("no of individuals in population: ", k)
    max_gen = 5 #earlier were 10
    delta = pi/8
    mu = 0.3
    rho = pi/16
    elitism = hqga_utils.ELITISM_Q

    if elitism == hqga_utils.ELITISM_Q or elitism == hqga_utils.ELITISM_D:
        params = hqga_utils.Parameters(k,max_gen,delta,mu, elitism)
    elif elitism == hqga_utils.ELITISM_R:
        params = hqga_utils.ReinforcementParameters(k,max_gen, delta, rho, mu)
    else:
        print("Please, select one elitism procedure among ELITISM_Q, ELITISM_D and ELITISM_R")

    #presentation hyper-parameters
    params.progressBar = True
    params.verbose = True
    params.draw_circuit = True
    # build circuit
    circuit = hqga_utils.setupCircuit(params.pop_size, problem.dim * problem.num_bit_code)
    gBest, chromosome_evolution, bests = hqga_algorithm.runQGA(device_features, circuit, params, problem)
    print("gBest.chr: ",gBest.chr)
    best_features = [index for index, char in enumerate(gBest.chr) if char == '1']
    print("best features: ",best_features)
    clf = RandomForestClassifier(random_state=42)
    clf.fit(train_x_sc[:, best_features], y_train)
    y_pred = clf.predict(test_x_sc[:, best_features])

    # Return accuracy as the fitness score
    accuracy = accuracy_score(y_test, y_pred)
    print("accuracy of selected best features: ", accuracy)

    return best_features, accuracy



In [12]:
best_features, accuracy = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=False)

no of individuals in population:  10


Generations:   0%|          | 0/6 [00:00<?, ?it/s]

        ┌───┐┌──────────┐ ░ ┌─┐                                                                                       
q194_0: ┤ H ├┤ Ry(-π/8) ├─░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░ └╥┘┌─┐                                                                                    
q194_1: ┤ H ├┤ Ry(π/8) ├──░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░  ║ └╥┘┌─┐                                                                                 
q194_2: ┤ H ├┤ Ry(π/8) ├──░──╫──╫─┤M├─────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┴┐ ░  ║  ║ └╥┘┌─┐                                                                              
q195_0: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫──╫─┤M├──────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░  ║  ║  ║ └╥┘┌─┐     

Generations:  17%|█▋        | 1/6 [00:19<01:39, 19.87s/it]

selected_features:  [1, 2]
Fitness values: [0.3162173913043478, 0.3162173913043478, 0.2747391304347826, 0.3172173913043478, 0.3172173913043478, 0.3705652173913043, 0.3162173913043478, 0.2737391304347826, 10000000.0, 0.2954782608695652]
Best fitness 0.2737391304347826 ; index best  7
        ┌───┐┌──────────┐ ░                 ░ ┌─────────┐  ░ ┌─┐                                                                                       
q194_0: ┤ H ├┤ Ry(-π/8) ├─░─────────────────░─┤ Ry(π/4) ├──░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░                 ░ ├─────────┴┐ ░ └╥┘┌─┐                                                                                    
q194_1: ┤ H ├┤ Ry(π/8) ├──░─────────────────░─┤ Ry(-π/4) ├─░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░                 ░ ├──────────┤ ░  ║ └╥┘┌─┐                                      

...

selected_features:  [1, 2]
selected_features:  [1, 2]
selected_features:  [2]
Fitness values: [0.2954782608695652, 0.3172173913043478, 0.2954782608695652, 10000000.0, 0.3162173913043478, 10000000.0, 0.2954782608695652, 10000000.0, 0.2954782608695652, 0.3162173913043478]
Best fitness 0.2954782608695652 ; index best  0
        ┌───┐┌──────────┐ ░                 ░              ░ ┌─┐                                                                                       
q194_0: ┤ H ├┤ Ry(-π/8) ├─░───■─────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░   │             ░              ░ └╥┘┌─┐                                                                                    
q194_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■────────░──────────────░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░   │    │        ░              ░  ║ └╥┘┌─┐   

Generations:  83%|████████▎ | 5/6 [01:32<00:18, 18.41s/it]

selected_features:  [2]
Fitness values: [0.2747391304347826, 0.3172173913043478, 0.3162173913043478, 10000000.0, 10000000.0, 10000000.0, 10000000.0, 10000000.0, 0.2747391304347826, 0.3162173913043478]
Best fitness 0.2747391304347826 ; index best  0
        ┌───┐┌──────────┐ ░                 ░              ░ ┌─┐                                                                                       
q194_0: ┤ H ├┤ Ry(-π/8) ├─░───■─────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░   │             ░              ░ └╥┘┌─┐                                                                                    
q194_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■────────░──────────────░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░   │    │        ░              ░  ║ └╥┘┌─┐                                                                         

Generations: 100%|██████████| 6/6 [01:47<00:00, 17.93s/it]

Fitness values: [0.2954782608695652, 0.3705652173913043, 0.3162173913043478, 0.3162173913043478, 0.2747391304347826, 10000000.0, 0.3705652173913043, 10000000.0, 0.28360869565217395, 0.3162173913043478]
Best fitness 0.2747391304347826 ; index best  4
The best chromosome is:  101
The best phenotype is:  101
Its fitness value is:  0.2737391304347826
The fitness evaluations to obtain the best:  10
The number of fitness evaluations is:  60
gBest.chr:  101
best features:  [0, 2]
accuracy of selected best features:  0.7282608695652174


In [13]:
# Q[123]

In [14]:
print("Balanced datasets under dimension 15: ====== ")

dir = "dim_under_15/balanced"

bal_data_res = []

for file in os.listdir(dir):
    print("dataset: ",file)
    f_p = os.path.join(dir, file)
    csv = pd.read_csv(f_p)
    
    target = csv.columns[-1]
    X = csv.drop([target], axis=1)
    y = csv[target]
    
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
    train_df = pd.concat([X_train, y_train], axis=1)
    test_df = pd.concat([X_test, y_test], axis=1)

    scaler = StandardScaler()
    train_x_sc = scaler.fit_transform(X_train)
    test_x_sc = scaler.transform(X_test)

    best_features, accuracy = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=True)

    bal_data_res.append([file, best_features, accuracy])

Balanced datasets under dimension 15: ====== 
dataset:  processed_Dishonest Internet users.csv
backend:  <IBMBackend('ibm_brisbane')>
no of individuals in population:  7


Generations:   0%|          | 0/6 [00:00<?, ?it/s]

        ┌───┐┌─────────┐  ░ ┌─┐                                                                                 
q204_0: ┤ H ├┤ Ry(π/8) ├──░─┤M├─────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░ └╥┘┌─┐                                                                              
q204_1: ┤ H ├┤ Ry(π/8) ├──░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░  ║ └╥┘┌─┐                                                                           
q204_2: ┤ H ├┤ Ry(π/8) ├──░──╫──╫─┤M├───────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░  ║  ║ └╥┘┌─┐                                                                        
q204_3: ┤ H ├┤ Ry(π/8) ├──░──╫──╫──╫─┤M├────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░  ║  ║  ║ └╥┘┌─┐                                                     

Generations:  17%|█▋        | 1/6 [00:22<01:54, 22.95s/it]

selected_features:  [1, 3]
selected_features:  [0, 2]
selected_features:  [0, 1, 2, 3]
Fitness values: [0.18756701030927836, 0.23811340206185572, 0.136020618556701, 0.15663917525773197, 0.15663917525773197, 0.09478350515463918, 0.004]
Best fitness 0.004 ; index best  6
                          ░ ┌───┐                ░              ░ ┌─┐                                                                                 
q204_0: ──────────────────░─┤ X ├────────────────░──────────────░─┤M├─────────────────────────────────────────────────────────────────────────────────
        ┌───┐┌─────────┐  ░ └─┬─┘                ░              ░ └╥┘┌─┐                                                                              
q204_1: ┤ H ├┤ Ry(π/8) ├──░───┼──────────────────░──────────────░──╫─┤M├──────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░   │                  ░              ░  ║ └╥┘┌─┐                                                   

...

selected_features:  [1, 2, 3, 4]
Fitness values: [0.377, 0.3213076923076923, 0.377, 0.377, 0.30207692307692313]
Best fitness 0.30207692307692313 ; index best  4
        ┌───┐┌──────────┐ ░                                ░              ░ ┌─┐                                                                                       
q443_0: ┤ H ├┤ Ry(-π/8) ├─░────────────────────────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░                                ░ ┌──────────┐ ░ └╥┘┌─┐                                                                                    
q443_1: ┤ H ├┤ Ry(π/8) ├──░────────────────────────────────░─┤ Ry(-π/4) ├─░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┤  ░                                ░ └──────────┘ ░  ║ └╥┘┌─┐                                                                                 
q443

Generations:  83%|████████▎ | 5/6 [03:23<00:50, 50.71s/it]

selected_features:  [2, 3, 5]
Fitness values: [0.377, 0.42607692307692313, 0.35776923076923073, 0.4443076923076923, 0.3106923076923077]
Best fitness 0.3106923076923077 ; index best  4
        ┌───┐┌──────────┐ ░                                ░              ░ ┌─┐                                                                                       
q443_0: ┤ H ├┤ Ry(-π/8) ├─░────────────────────────────────░──────────────░─┤M├───────────────────────────────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░                                ░ ┌─────────┐  ░ └╥┘┌─┐                                                                                    
q443_1: ┤ H ├┤ Ry(-π/8) ├─░────────────────────────────────░─┤ Ry(π/4) ├──░──╫─┤M├────────────────────────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░                                ░ ├─────────┴┐ ░  ║ └╥┘┌─┐                                                               

Generations: 100%|██████████| 6/6 [04:50<00:00, 48.44s/it]

selected_features:  [1, 3, 5]
Fitness values: [0.377, 0.377, 0.35776923076923073, 0.3972307692307693, 0.41646153846153844]
Best fitness 0.35776923076923073 ; index best  2
The best chromosome is:  111101
The best phenotype is:  111101
Its fitness value is:  0.24538461538461542
The fitness evaluations to obtain the best:  10
The number of fitness evaluations is:  30
gBest.chr:  111101
best features:  [0, 1, 2, 3, 5]
accuracy of selected best features:  0.7596153846153846


In [15]:
bal_data_res

[['processed_Dishonest Internet users.csv', [0, 2, 3], 1.0],
 ['processed_Habermans Survival.csv', [0, 2], 0.7282608695652174],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8],
 ['processed_ILPD (Indian Liver Patient Dataset).csv',
  [0, 1, 4, 5, 7, 8, 9],
  0.7428571428571429],
 ['processed_Liver Disorders.csv', [0, 1, 2, 3, 5], 0.7596153846153846]]

In [16]:
print("Imbalanced datasets under dimension 15: ====== ")

dir = "dim_under_15/imbalanced"

imbal_data_res = []

for file in os.listdir(dir):
    print("dataset: ",file)
    f_p = os.path.join(dir, file)
    csv = pd.read_csv(f_p)
    
    target = csv.columns[-1]
    X = csv.drop([target], axis=1)
    y = csv[target]
    
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
    train_df = pd.concat([X_train, y_train], axis=1)
    test_df = pd.concat([X_test, y_test], axis=1)

    scaler = StandardScaler()
    train_x_sc = scaler.fit_transform(X_train)
    test_x_sc = scaler.transform(X_test)

    best_features, accuracy = runFeatSel(train_x_sc, y_train, test_x_sc, y_test, real_quantum_hardware=True)

    imbal_data_res.append([file, best_features, accuracy])

Imbalanced datasets under dimension 15: ====== 
dataset:  processed_Abalone.csv
backend:  <IBMBackend('ibm_brisbane')>
no of individuals in population:  3


Generations:   0%|          | 0/6 [00:00<?, ?it/s]

        ┌───┐┌─────────┐  ░ ┌─┐                                                                     
q501_0: ┤ H ├┤ Ry(π/8) ├──░─┤M├─────────────────────────────────────────────────────────────────────
        ├───┤├─────────┴┐ ░ └╥┘┌─┐                                                                  
q501_1: ┤ H ├┤ Ry(-π/8) ├─░──╫─┤M├──────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░  ║ └╥┘┌─┐                                                               
q501_2: ┤ H ├┤ Ry(π/8) ├──░──╫──╫─┤M├───────────────────────────────────────────────────────────────
        ├───┤├─────────┴┐ ░  ║  ║ └╥┘┌─┐                                                            
q501_3: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫──╫─┤M├────────────────────────────────────────────────────────────
        ├───┤├──────────┤ ░  ║  ║  ║ └╥┘┌─┐                                                         
q501_4: ┤ H ├┤ Ry(-π/8) ├─░──╫──╫──╫──╫─┤M├────────────────────────────────────────────────

Generations:  17%|█▋        | 1/6 [00:37<03:08, 37.78s/it]

Fitness values: [0.11522805805114034, 0.12359433310297163, 0.12303939184519697]
Best fitness 0.11522805805114034 ; index best  0
        ┌───┐┌─────────┐  ░                                          ░             ░ ┌─┐                                                                     
q501_0: ┤ H ├┤ Ry(π/8) ├──░───■──────────────────────────────────────░─────────────░─┤M├─────────────────────────────────────────────────────────────────────
        ├───┤├─────────┴┐ ░   │                                      ░             ░ └╥┘┌─┐                                                                  
q501_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■─────────────────────────────────░─────────────░──╫─┤M├──────────────────────────────────────────────────────────────────
        ├───┤├─────────┬┘ ░   │    │                                 ░             ░  ║ └╥┘┌─┐                                                               
q501_2: ┤ H ├┤ Ry(π/8) ├──░───┼────┼────■────────────────────────────░───────────

...

Fitness values: [0.1959918699186992, 0.1847967479674797]
Best fitness 0.1847967479674797 ; index best  1
                           ░ ┌───┐                                                             ░  ░ ┌─┐                                                                           
 q797_0: ──────────────────░─┤ X ├─────────────────────────────────────────────────────────────░──░─┤M├───────────────────────────────────────────────────────────────────────────
                           ░ └─┬─┘┌───┐                                                        ░  ░ └╥┘┌─┐                                                                        
 q797_1: ──────────────────░───┼──┤ X ├────────────────────────────────────────────────────────░──░──╫─┤M├────────────────────────────────────────────────────────────────────────
                           ░   │  └─┬─┘┌───┐                                                   ░  ░  ║ └╥┘┌─┐                                                                     


Generations:  83%|████████▎ | 5/6 [20:20<04:39, 279.53s/it]

         ┌───┐┌─────────┐  ░                                                                   ░  ░ ┌─┐                                                                           
 q797_0: ┤ H ├┤ Ry(π/8) ├──░───■───────────────────────────────────────────────────────────────░──░─┤M├───────────────────────────────────────────────────────────────────────────
         ├───┤├─────────┴┐ ░   │                                                               ░  ░ └╥┘┌─┐                                                                        
 q797_1: ┤ H ├┤ Ry(-π/8) ├─░───┼────■──────────────────────────────────────────────────────────░──░──╫─┤M├────────────────────────────────────────────────────────────────────────
         ├───┤├─────────┬┘ ░   │    │                                                          ░  ░  ║ └╥┘┌─┐                                                                     
 q797_2: ┤ H ├┤ Ry(π/8) ├──░───┼────┼────■─────────────────────────────────────────────────────░──░──╫──╫

Generations: 100%|██████████| 6/6 [21:37<00:00, 216.27s/it]

Fitness values: [0.1959918699186992, 0.1959918699186992]
Best fitness 0.1959918699186992 ; index best  0
The best chromosome is:  0010110111010
The best phenotype is:  0010110111010
Its fitness value is:  0.15334146341463417
The fitness evaluations to obtain the best:  2
The number of fitness evaluations is:  12
gBest.chr:  0010110111010
best features:  [2, 4, 5, 7, 8, 9, 11]
accuracy of selected best features:  0.8536585365853658


In [17]:
bal_data_res

[['processed_Dishonest Internet users.csv', [0, 2, 3], 1.0],
 ['processed_Habermans Survival.csv', [0, 2], 0.7282608695652174],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8],
 ['processed_ILPD (Indian Liver Patient Dataset).csv',
  [0, 1, 4, 5, 7, 8, 9],
  0.7428571428571429],
 ['processed_Liver Disorders.csv', [0, 1, 2, 3, 5], 0.7596153846153846]]

In [18]:
imbal_data_res

[['processed_Abalone.csv', [0, 1, 4, 5, 6], 0.8899447131997236],
 ['processed_Blood Transfusion Service.csv', [0, 2, 3], 0.783625730994152],
 ['processed_Breast Cancer.csv', [0, 3, 4, 5, 6, 7, 8], 0.8473282442748091],
 ['processed_Climate Model Simulation Crashes.csv', [0], 0.8417508417508418],
 ['processed_Fertility.csv', [0, 1, 2, 3, 6, 8], 0.9622641509433962],
 ['processed_Heart Disease.csv', [2, 4, 5, 7, 8, 9, 11], 0.8536585365853658]]

In [19]:
bal_data_res + imbal_data_res

[['processed_Dishonest Internet users.csv', [0, 2, 3], 1.0],
 ['processed_Habermans Survival.csv', [0, 2], 0.7282608695652174],
 ['processed_Hayes Roth.csv', [1, 2, 3], 0.8],
 ['processed_ILPD (Indian Liver Patient Dataset).csv',
  [0, 1, 4, 5, 7, 8, 9],
  0.7428571428571429],
 ['processed_Liver Disorders.csv', [0, 1, 2, 3, 5], 0.7596153846153846],
 ['processed_Abalone.csv', [0, 1, 4, 5, 6], 0.8899447131997236],
 ['processed_Blood Transfusion Service.csv', [0, 2, 3], 0.783625730994152],
 ['processed_Breast Cancer.csv', [0, 3, 4, 5, 6, 7, 8], 0.8473282442748091],
 ['processed_Climate Model Simulation Crashes.csv', [0], 0.8417508417508418],
 ['processed_Fertility.csv', [0, 1, 2, 3, 6, 8], 0.9622641509433962],
 ['processed_Heart Disease.csv', [2, 4, 5, 7, 8, 9, 11], 0.8536585365853658]]

In [20]:
res_data = pd.DataFrame(bal_data_res + imbal_data_res)
res_data.columns = ["Dataset", "Best Features", "Accuracy"]
res_data.to_csv("dim_under_15/res/res_REAL.csv", index=None)